In [109]:

import matplotlib.pyplot as plt
import pygame
import numpy as np
import math
import random
import copy
import tensorflow as tf
from tensorflow import keras




In [110]:
#### C'est le premier algo. Mutation uniquement. Pas de selection des meilleurs. 
### Tres limité

In [111]:
##### CONSTANTES

f = 0.3
rb = 5
rt = 20
dt = 0.0
m = 1
g = 9.81
k = 2
height = 700
width = 700
num_elites = 1
nb_gen =5
nb_pop = 50
mutation_rate = 1/150
v_max = 30
input_size = 14

In [112]:
###### FONCTIONS UTILES

def produitvectoriel(vect1,vect2):
    return (vect1[0]*vect2[1] - vect1[1]*vect2[0])

def produitscalaire(vect1,vect2):
    return(vect1[0]*vect2[0] + vect1[1]*vect2[1])


In [113]:
##### CLASSE JOUEUR


class Joueur:
    
    
    
    def __init__(self, array_trou,array_balle,obstacles):
        self.is_best = False
        self.fitness = 0
        self.partie = Partie(array_balle,array_trou,obstacles)
        self.liste_emplacements = [array_balle]
        self.Segment_radar = self.radar()
        self.Distance_obstacle = self.reperer_obstacle()
        self.cerveau = NeuralNetwork()
        self.couleur = (random.randint(0,250),random.randint(0,250),random.randint(0,250))
        self.nbre_mouvements = 0
      

    def radar(self):
        radar = []
        angle = [0,np.pi/4,np.pi/3,2*np.pi/3,3*np.pi/4,np.pi,5*np.pi/4,4*np.pi/3,5*np.pi/3,7*np.pi/4]
        for i in angle:
            segment = Segment(self.partie.balle.position, [self.partie.balle.position[0]+np.cos(i)*50,self.partie.balle.position[1]+np.sin(i)*50])
            radar.append(segment)
            #segment.print_segment()
        return radar
    
    def reperer_obstacle(self):
        self.radar()
        distances = []
        for i in self.Segment_radar:
            croisement = [50]
            for j in self.partie.obstacles : 
                if i.cross(j) :
                    if j.arrivee[0]==j.depart[0]: 
                        x_crois = j.arrivee[0]
                    else :
                        x_crois = (i.ordonnee()-j.ordonnee())/(j.pente()-i.pente())
                    y_crois = i.pente()*x_crois + i.ordonnee()
                    croisement.append(np.sqrt((x_crois - self.partie.balle.position[0])**2 + (y_crois - self.partie.balle.position[1])**2 ))
            distances.append(min(croisement))
        return [i/50 for i in distances]
            
                    
        
    def evaluate_fitness(self):
        
        distance = np.sqrt((self.partie.trou.position[0] - self.partie.balle.position[0])**2 + (self.partie.trou.position[1] - self.partie.balle.position[1])**2 )
        
        if self.partie.reached_goal:
            self.fitness = 100
        
        else: 
            self.fitness = 100/distance**2 
           
            
        
    def faire_moves(self):
    
        while self.partie.is_dead == False and self.nbre_mouvements < 20 :
            Array_inputs = self.reperer_obstacle()
            Array_inputs.append(self.partie.balle.position[0]/width)
            Array_inputs.append(self.partie.trou.position[0]/width)
            Array_inputs.append(self.partie.balle.position[1]/width)
            Array_inputs.append(self.partie.trou.position[1]/width)
            inputs = self.cerveau.array_to_tensor(np.array([Array_inputs]))
            outputs = self.cerveau.model.predict(inputs)
            self.liste_emplacements.append(self.partie.deplacement([outputs[0][0]*v_max,outputs[0][1]*2*np.pi]))
            self.nbre_mouvements +=1
            
        print("fin des move")
    
    def mutate(self):
        weights = self.cerveau.model.get_weights()
        for i in range(len(self.cerveau.model.get_weights()[0])):
            for j in range(len(self.cerveau.model.get_weights()[0][0])):
                if random.random() < mutation_rate:
                    weights[0][i][j] = random.uniform(-0.5,0.5)
        self.cerveau.model.set_weights(weights)
        

                

In [114]:
##### CLASSE NEURAL NETWORK

class NeuralNetwork:
    def __init__(self):
        self.model = keras.Sequential([
        keras.layers.Dense(15, input_shape=(input_size,),
        activation=tf.nn.relu,),
        keras.layers.Dense(2,
        activation=tf.nn.sigmoid)
        ])
        
    def array_to_tensor(self, array):
        '''Convert numpy array to tensor object'''
        tensor_data = tf.convert_to_tensor(array, dtype=tf.float32)
        return tensor_data    
    

    def copy(self):
        Nouvelle_copie = NeuralNetwork() 
        Nouvelle_copie.model.set_weights(self.model.get_weights())
        return Nouvelle_copie


'''
cerveau = NeuralNetwork()
inputs = cerveau.array_to_tensor(np.array([[1,2,3,4,5,6,7,8,9,10,11,12,13]]))
cerveau_copy = cerveau.copy()
#print(cerveau_copy.model.get_weights())
cerveau2 = NeuralNetwork()
cerveau.model.set_weights(cerveau2.model.get_weights())
cerveau_copy2 = cerveau.copy()
#print(cerveau_copy2.model.get_weights())
print(cerveau_copy2.model.get_weights()[0][0])

output = cerveau.model.predict(inputs)
print(output[0][0])
'''


'\ncerveau = NeuralNetwork()\ninputs = cerveau.array_to_tensor(np.array([[1,2,3,4,5,6,7,8,9,10,11,12,13]]))\ncerveau_copy = cerveau.copy()\n#print(cerveau_copy.model.get_weights())\ncerveau2 = NeuralNetwork()\ncerveau.model.set_weights(cerveau2.model.get_weights())\ncerveau_copy2 = cerveau.copy()\n#print(cerveau_copy2.model.get_weights())\nprint(cerveau_copy2.model.get_weights()[0][0])\n\noutput = cerveau.model.predict(inputs)\nprint(output[0][0])\n'

In [115]:
###### CLASSE POPULATION

class Population:
    def __init__(self, size, arraytrou, arrayballe, obstacles):
        self.liste_joueur = []
        self.liste_nbre_mouvements = []
        self.nbr_winner = 0
        for i in range(size):
            self.liste_joueur.append(Joueur(arraytrou, arrayballe, obstacles))
    '''
    def mutate_all(self,arraytrou, arrayballe, obstacles):
        for i in range(len(self.liste_joueur)):
            self.liste_joueur[i].partie = Partie(arrayballe,arraytrou,obstacles)
            nouveauJoueur = Joueur(arraytrou, arrayballe, obstacles)
            nouveauJoueur.mutate()
            self.liste_joueur[i].faire_moves()
            self.liste_joueur[i].evaluate_fitness()
            nouveauJoueur.faire_moves()
            nouveauJoueur.evaluate_fitness()
            #print("nb_coups du vieux : "+ str(self.liste_joueur[i].partie.nb_coups))
            #print("nb_coups du jeune : "+ str(nouveauJoueur.partie.nb_coups))
            if nouveauJoueur.fitness > self.liste_joueur[i].fitness :
                self.liste_joueur[i] = nouveauJoueur
    '''  
    
    def are_all_dead(self):
        for j in self.liste_joueur: 
            if j.partie.is_dead == False and j.partie.reached_goal == False :
                return False
        return True
        
    def step_ga(self,size, arraytrou,arrayballe,obstacles):
        liste = []
        
        #On continue de faire bouger chaque boule tant qu'elles ne sont pas toutes mortes
        while not self.are_all_dead():
            for j in range(len(self.liste_joueur)): 
                print("joueur numero : " + str(j) + "is moving")
                self.liste_joueur[j].faire_moves()
                
        #On evalue la fitness de chacun    
        for j in range(len(self.liste_joueur)): 
            self.liste_nbre_mouvements.append(self.liste_joueur[j].nbre_mouvements)
            self.liste_joueur[j].evaluate_fitness()
            #print("joueur numero : " + str(j) + " a une fitnesse de : " +  str(self.liste_joueur[j].fitness) )
            #print("et un cerveau : " + str(self.liste_joueur[j].cerveau.model.get_weights()[0][0][0]))
            #print("nbre de coups : " + str(self.liste_joueur[j].nbre_mouvements))
            if self.liste_joueur[j].partie.reached_goal :
                self.nbr_winner +=1
        print("le nombre de gagnant est : "+ str(self.nbr_winner))   

            
      #  fits = [self.liste_joueur[i].fitness for i in range(nb_pop)]
        self.liste_joueur = sorted(self.liste_joueur, key=lambda joueur: joueur.fitness, reverse = True)
        for i in range(num_elites):
            self.liste_joueur[i].couleur = (255,0,0)
            self.liste_joueur[i].nbre_mouvements = 0
            self.liste_joueur[i].liste_emplacements = [self.liste_joueur[i].partie.balle.position]
            self.liste_joueur[i].partie.is_dead = False
            self.liste_joueur[i].partie.reached_goal = False 
            liste.append(self.liste_joueur[i])
            
            
            
            
        for i in range(num_elites,nb_pop):
            parent = self.tournament_selection(k)
            partie = Partie(arrayballe,arraytrou,obstacles)
            child = Joueur(arraytrou, arrayballe, obstacles)
            child.partie = partie
            child.cerveau = parent.cerveau.copy()
            child.mutate()
            liste.append(child)
            
        self.liste_joueur = liste
        
        
    def tournament_selection(self, k):
        select = []
        for i in range(k):
            select.append(random.randint(0,nb_pop-1))
        best = select[0]
        for j in select:
            if self.liste_joueur[j].fitness > self.liste_joueur[best].fitness:
                best = j
        return self.liste_joueur[best]   
        
                
    def print_partie(self,arraytrou, arrayballe, obstacles):
        pygame.init()
        win = pygame.display.set_mode((700,700))
        pygame.display.set_caption("Le mini-golf de l'enfer")
        x_trou = int(arraytrou[0])
        y_trou = int(arraytrou[1])
        win.fill((0,128,0))
        for i in obstacles:
            pygame.draw.line(win, (0,0,0), i.depart, i.arrivee,10)

        run = True
        couleur = self.generer_couleur()
        while run :

            for i in range(max(self.liste_nbre_mouvements)): 
                pygame.time.delay(10)
                for event in pygame.event.get():
                    if event.type == pygame.QUIT:
                        run = False
                pygame.draw.circle(win, (0,0,0), (x_trou,y_trou), rt)
                for obs in obstacles:
                    pygame.draw.line(win, (0,0,0), obs.depart, obs.arrivee,10)
                for j in self.liste_joueur:
                    pygame.draw.circle(win, j.couleur, (int(j.liste_emplacements[min(i,j.nbre_mouvements)][0]),int(j.liste_emplacements[min(i,j.nbre_mouvements)][1])), rb)
                    pygame.display.update()
                win.fill((0,128,0))
        print("fin")
        pygame.display.flip()
        pygame.quit()



In [116]:
#### CLASSE SEGMENT

class Segment:
    def __init__(self,array1,array2):
        self.depart = array1
        self.arrivee = array2
        
    def cross(self , segment):
        ab = [self.arrivee[0] - self.depart[0] , self.arrivee[1] - self.depart[1]]
        apbp = [segment.arrivee[0] - segment.depart[0] , segment.arrivee[1] - segment.depart[1]]
        abp = [segment.arrivee[0] - self.depart[0], segment.arrivee[1] - self.depart[1]]
        aap = [segment.depart[0] - self.depart[0], segment.depart[1] - self.depart[1] ]
        apb = [self.arrivee[0] - segment.depart[0] , self.arrivee[1] - segment.depart[1]]
        apa = [self.depart[0] - segment.depart[0] , self.depart[1] - segment.depart[1]]
        
        c1 = produitvectoriel(ab,apbp) != 0
        c2 = (produitvectoriel(ab,abp) * produitvectoriel(ab,aap))<=0
        c3 = (produitvectoriel(apbp,apb) * produitvectoriel(apbp,apa))<=0
        return(c1 and c2 and c3)
    
    def pente(self):
        return (self.arrivee[1]-self.depart[1])/(self.arrivee[0]-self.depart[0])
    def ordonnee(self):
        return (self.depart[1]-self.pente()*self.depart[0])
    def print_segment(self) :
        print([self.depart, self.arrivee])

In [117]:

##### CLASSE TROU

class Trou:
    def __init__(self, array):
        self.position = array.copy()
 


In [118]:
##### CLASSE BALLE

class Balle:
    def __init__(self, array):
        self.position = array.copy()


In [119]:
##### CLASSE PARTIE

class Partie:
    def __init__(self, arrayballe,arraytrou, obstacles):
        self.balle = Balle(arrayballe)
        self.trou = Trou(arraytrou)
        self.obstacles = obstacles
        self.is_dead = False
        self.reached_goal = False 
        
    def is_won(self):
        distance = np.sqrt((self.trou.position[0] - self.balle.position[0])**2 + (self.trou.position[1] - self.balle.position[1])**2 )
       # print(distance)
        if distance < rt :
            self.reached_goal = True
    
    def is_possible_move(self,segment_dep):
        liste_obstacles_cross = []
        for i in self.obstacles: # Pour tous les obstacles
            if i.cross(segment_dep): # Si un segment_dep et i se croisent alors le move n'est pas possible
                    liste_obstacles_cross.append(i)
        if len(liste_obstacles_cross) > 0 :
            liste_distances = []
            liste_inter = []
            for i in liste_obstacles_cross:
                if (segment_dep.depart[0] - segment_dep.arrivee[0] == 0):
                    a_i = (i.depart[1] - i.arrivee[1]) / (i.depart[0] - i.arrivee[0])
                    b_i = i.depart[1] - a_i *i.depart[0]
                    x_inter = segment_dep.depart[0]
                    y_inter = a_i * x_inter + b_i
                    liste_inter.append([x_inter , y_inter])
                    
                    
                elif (i.depart[0] - i.arrivee[0] == 0):
                    a_segment_dep = (segment_dep.depart[1] - segment_dep.arrivee[1]) / (segment_dep.depart[0] - segment_dep.arrivee[0])
                    b_segment_dep = segment_dep.depart[1] - a_segment_dep * segment_dep.depart[0]
                    x_inter = i.depart[0]
                    y_inter = a_segment_dep * x_inter + b_segment_dep
                    liste_inter.append([x_inter , y_inter])
                
                else :
                    a_segment_dep = (segment_dep.depart[1] - segment_dep.arrivee[1]) / (segment_dep.depart[0] - segment_dep.arrivee[0])
                    b_segment_dep = segment_dep.depart[1] - a_segment_dep * segment_dep.depart[0]
                    a_i = (i.depart[1] - i.arrivee[1]) / (i.depart[0] - i.arrivee[0])
                    b_i = i.depart[1] - a_i *i.depart[0]
                    x_inter = (b_i - b_segment_dep) / (a_segment_dep - a_i)
                    y_inter = a_i * x_inter + b_i
                    liste_inter.append([x_inter , y_inter])
                
                liste_distances.append(np.sqrt( (x_inter - self.balle.position[0])**2 + (y_inter - self.balle.position[1])**2))
            self.balle.position[0] = liste_inter[liste_distances.index(min(liste_distances))][0]
            self.balle.position[1] = liste_inter[liste_distances.index(min(liste_distances))][1]
                
            return False
        return True
    
    
    def deplacement(self,vitesse_initiale): # La vitesse sera de la forme [ ||v|| , theta)]
        distance =0.5*m/f*vitesse_initiale[0]**2
       # print(vitesse_initiale[0])
        segment_dep = Segment([self.balle.position[0],self.balle.position[1]],[self.balle.position[0] + np.cos(vitesse_initiale[1]) * distance,self.balle.position[1] + np.sin(vitesse_initiale[1]) * distance] )
        self.is_won()
        
        if self.reached_goal:
            return (self.balle.position[0],self.balle.position[1])
        if self.is_possible_move(segment_dep):
            self.balle.position[0] += np.cos(vitesse_initiale[1]) * distance
            self.balle.position[1] += np.sin(vitesse_initiale[1]) * distance  
        else :
            self.is_dead = True
        return (self.balle.position[0],self.balle.position[1])
    
    def plot_fitness(self):
        mat = np.zeros((700,700))
        for i in range(700):
            for j in range(700):
                mat[i,j] = np.sqrt((self.trou.position[0] - i)**2 + (self.trou.position[1] - j)**2 )
        return mat





In [120]:
#DEFINITION DE LA PARTIE
obstacles = []
# On ajoute les murs
obstacles.append(Segment([0,0],[0,700]))
obstacles.append(Segment([0,0],[700,0]))
obstacles.append(Segment([700,0],[700,700]))
obstacles.append(Segment([0,700],[700,700]))
# On ajoute les obstacles
#obstacles.append(Segment([300,300],[900,300]))
#obstacles.append(Segment([0,400],[400,400]))


array_balle = [300,600]
array_trou = [300,300]
population = Population(nb_pop, array_trou, array_balle, obstacles)
#partie = Partie(array_balle,array_trou, obstacles)

'''
plt.figure(1)
mat = partie.plot_fitness()
im1 = plt.matshow(mat)
plt.title("Fitness")
plt.colorbar(im1)
plt.plot([])
plt.show()
'''

sumfits = []
for i in range(nb_gen):
    for j in range(len(population.liste_joueur)):
        population.liste_joueur[j].partie = Partie(array_balle,array_trou,obstacles) # On reset la partie
        population.liste_joueur[j].liste_emplacements = [array_balle]
    print("Calculating generation : "+str(i+1))
    population.step_ga(nb_pop, array_trou,array_balle,obstacles)
    fits = [population.liste_joueur[i].fitness for i in range(nb_pop)]
    sumfits.append(sum(fits))
    print("---")
    
    

plt.figure(2)
plt.plot(sumfits)
plt.show()

    

#population.print_partie(array_trou, array_balle, obstacles)
    
    
print("La simulation est terminée.")
    








Calculating generation : 1
joueur numero : 0is moving
fin des move
joueur numero : 1is moving
fin des move
joueur numero : 2is moving
fin des move
joueur numero : 3is moving
fin des move
joueur numero : 4is moving
fin des move
joueur numero : 5is moving
fin des move
joueur numero : 6is moving
fin des move
joueur numero : 7is moving
fin des move
joueur numero : 8is moving
fin des move
joueur numero : 9is moving
fin des move
joueur numero : 10is moving
fin des move
joueur numero : 11is moving
fin des move
joueur numero : 12is moving
fin des move
joueur numero : 13is moving
fin des move
joueur numero : 14is moving
fin des move
joueur numero : 15is moving
fin des move
joueur numero : 16is moving
fin des move
joueur numero : 17is moving
fin des move
joueur numero : 18is moving
fin des move
joueur numero : 19is moving
fin des move
joueur numero : 20is moving
fin des move
joueur numero : 21is moving
fin des move
joueur numero : 22is moving
fin des move
joueur numero : 23is moving
fin des move

fin des move
joueur numero : 47is moving
fin des move
joueur numero : 48is moving
fin des move
joueur numero : 49is moving
fin des move
le nombre de gagnant est : 2
---
Calculating generation : 5
joueur numero : 0is moving
fin des move
joueur numero : 1is moving
fin des move
joueur numero : 2is moving
fin des move
joueur numero : 3is moving
fin des move
joueur numero : 4is moving
fin des move
joueur numero : 5is moving
fin des move
joueur numero : 6is moving
fin des move
joueur numero : 7is moving
fin des move
joueur numero : 8is moving
fin des move
joueur numero : 9is moving
fin des move
joueur numero : 10is moving
fin des move
joueur numero : 11is moving
fin des move
joueur numero : 12is moving
fin des move
joueur numero : 13is moving
fin des move
joueur numero : 14is moving
fin des move
joueur numero : 15is moving
fin des move
joueur numero : 16is moving
fin des move
joueur numero : 17is moving
fin des move
joueur numero : 18is moving
fin des move
joueur numero : 19is moving
fin des

fin des move
joueur numero : 28is moving
fin des move
joueur numero : 29is moving
fin des move
joueur numero : 30is moving
fin des move
joueur numero : 31is moving
fin des move
joueur numero : 32is moving
fin des move
joueur numero : 33is moving
fin des move
joueur numero : 34is moving
fin des move
joueur numero : 35is moving
fin des move
joueur numero : 36is moving
fin des move
joueur numero : 37is moving
fin des move
joueur numero : 38is moving
fin des move
joueur numero : 39is moving
fin des move
joueur numero : 40is moving
fin des move
joueur numero : 41is moving
fin des move
joueur numero : 42is moving
fin des move
joueur numero : 43is moving
fin des move
joueur numero : 44is moving
fin des move
joueur numero : 45is moving
fin des move
joueur numero : 46is moving
fin des move
joueur numero : 47is moving
fin des move
joueur numero : 48is moving
fin des move
joueur numero : 49is moving
fin des move
joueur numero : 0is moving
fin des move
joueur numero : 1is moving
fin des move
joueu

fin des move
joueur numero : 22is moving
fin des move
joueur numero : 23is moving
fin des move
joueur numero : 24is moving
fin des move
joueur numero : 25is moving
fin des move
joueur numero : 26is moving
fin des move
joueur numero : 27is moving
fin des move
joueur numero : 28is moving
fin des move
joueur numero : 29is moving
fin des move
joueur numero : 30is moving
fin des move
joueur numero : 31is moving
fin des move
joueur numero : 32is moving
fin des move
joueur numero : 33is moving
fin des move
joueur numero : 34is moving
fin des move
joueur numero : 35is moving
fin des move
joueur numero : 36is moving
fin des move
joueur numero : 37is moving
fin des move
joueur numero : 38is moving
fin des move
joueur numero : 39is moving
fin des move
joueur numero : 40is moving
fin des move
joueur numero : 41is moving
fin des move
joueur numero : 42is moving
fin des move
joueur numero : 43is moving
fin des move
joueur numero : 44is moving
fin des move
joueur numero : 45is moving
fin des move
jou

fin des move
joueur numero : 17is moving
fin des move
joueur numero : 18is moving
fin des move
joueur numero : 19is moving
fin des move
joueur numero : 20is moving
fin des move
joueur numero : 21is moving
fin des move
joueur numero : 22is moving
fin des move
joueur numero : 23is moving
fin des move
joueur numero : 24is moving
fin des move
joueur numero : 25is moving
fin des move
joueur numero : 26is moving
fin des move
joueur numero : 27is moving
fin des move
joueur numero : 28is moving
fin des move
joueur numero : 29is moving
fin des move
joueur numero : 30is moving
fin des move
joueur numero : 31is moving
fin des move
joueur numero : 32is moving
fin des move
joueur numero : 33is moving
fin des move
joueur numero : 34is moving
fin des move
joueur numero : 35is moving
fin des move
joueur numero : 36is moving
fin des move
joueur numero : 37is moving
fin des move
joueur numero : 38is moving
fin des move
joueur numero : 39is moving
fin des move
joueur numero : 40is moving
fin des move
jou

...

fin des move
joueur numero : 8is moving
fin des move
joueur numero : 9is moving
fin des move
joueur numero : 10is moving
fin des move
joueur numero : 11is moving
fin des move
joueur numero : 12is moving
fin des move
joueur numero : 13is moving
fin des move
joueur numero : 14is moving
fin des move
joueur numero : 15is moving
fin des move
joueur numero : 16is moving
fin des move
joueur numero : 17is moving
fin des move
joueur numero : 18is moving
fin des move
joueur numero : 19is moving
fin des move
joueur numero : 20is moving
fin des move
joueur numero : 21is moving
fin des move
joueur numero : 22is moving
fin des move
joueur numero : 23is moving
fin des move
joueur numero : 24is moving
fin des move
joueur numero : 25is moving
fin des move
joueur numero : 26is moving
fin des move
joueur numero : 27is moving
fin des move
joueur numero : 28is moving
fin des move
joueur numero : 29is moving
fin des move
joueur numero : 30is moving
fin des move
joueur numero : 31is moving
fin des move
joueu

fin des move
joueur numero : 47is moving
fin des move
joueur numero : 48is moving
fin des move
joueur numero : 49is moving
fin des move
joueur numero : 0is moving
fin des move
joueur numero : 1is moving
fin des move
joueur numero : 2is moving
fin des move
joueur numero : 3is moving
fin des move
joueur numero : 4is moving
fin des move
joueur numero : 5is moving
fin des move
joueur numero : 6is moving
fin des move
joueur numero : 7is moving
fin des move
joueur numero : 8is moving
fin des move
joueur numero : 9is moving
fin des move
joueur numero : 10is moving
fin des move
joueur numero : 11is moving
fin des move
joueur numero : 12is moving
fin des move
joueur numero : 13is moving
fin des move
joueur numero : 14is moving
fin des move
joueur numero : 15is moving
fin des move
joueur numero : 16is moving
fin des move
joueur numero : 17is moving
fin des move
joueur numero : 18is moving
fin des move
joueur numero : 19is moving
fin des move
joueur numero : 20is moving
fin des move
joueur numero

joueur numero : 6is moving
fin des move
joueur numero : 7is moving
fin des move
joueur numero : 8is moving
fin des move
joueur numero : 9is moving
fin des move
joueur numero : 10is moving
fin des move
joueur numero : 11is moving
fin des move
joueur numero : 12is moving
fin des move
joueur numero : 13is moving
fin des move
joueur numero : 14is moving
fin des move
joueur numero : 15is moving
fin des move
joueur numero : 16is moving
fin des move
joueur numero : 17is moving
fin des move
joueur numero : 18is moving
fin des move
joueur numero : 19is moving
fin des move
joueur numero : 20is moving
fin des move
joueur numero : 21is moving
fin des move
joueur numero : 22is moving
fin des move
joueur numero : 23is moving
fin des move
joueur numero : 24is moving
fin des move
joueur numero : 25is moving
fin des move
joueur numero : 26is moving
fin des move
joueur numero : 27is moving
fin des move
joueur numero : 28is moving
fin des move
joueur numero : 29is moving
fin des move
joueur numero : 30is

fin des move
joueur numero : 7is moving
fin des move
joueur numero : 8is moving
fin des move
joueur numero : 9is moving
fin des move
joueur numero : 10is moving
fin des move
joueur numero : 11is moving
fin des move
joueur numero : 12is moving
fin des move
joueur numero : 13is moving
fin des move
joueur numero : 14is moving
fin des move
joueur numero : 15is moving
fin des move
joueur numero : 16is moving
fin des move
joueur numero : 17is moving
fin des move
joueur numero : 18is moving
fin des move
joueur numero : 19is moving
fin des move
joueur numero : 20is moving
fin des move
joueur numero : 21is moving
fin des move
joueur numero : 22is moving
fin des move
joueur numero : 23is moving
fin des move
joueur numero : 24is moving
fin des move
joueur numero : 25is moving
fin des move
joueur numero : 26is moving
fin des move
joueur numero : 27is moving
fin des move
joueur numero : 28is moving
fin des move
joueur numero : 29is moving
fin des move
joueur numero : 30is moving
fin des move
joueur

KeyboardInterrupt: 